In [1]:
"""This script will use esm models to visualize embeddings of proteins from SKEMPI datasets"""
import torch
import esm
import pandas as pd
import scanpy as sc
import numpy as np
from fuzzywuzzy import fuzz

In [27]:
# retrieve all proteins from the dataset
#df = pd.read_csv('USE__mutant_seqswoscore.csv', index_col=0)
df = pd.read_csv('skempiwmutants_nanincl.csv', index_col=0)
df = df[['pdb','Mutation(s)_PDB', 'Affinity_mut (M)', 'Affinity_wt (M)', 'Protein 1', 'Protein 2', 'wild_seq1', 'wild_seq2', 'mutant_seq']]
df

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12244  3QIB           TP12A         >1.1E-03         5.5E-06   
12245  3QIB           TP12S         3.38E-05         5.5E-06   
12246  3QIB           TP12N         4.34E-05         5.5E-06   
12247  3QIB      YP7F,TP12S         4.29E-05         5.5E-06   
12248  3QIB      YP7F,TP12S         4.29E-05         5.5E-06   

                   Protein 1 Protein 2  \
0       Subtilisin Carlsberg   Eglin c   
1       Subtilisin Carlsberg   Eglin c   
2       Subtilisin Carlsberg   Eglin c   
3       Subtilisin Carlsberg   Eglin c   
4       Subtilisin Carlsberg   Eglin c   
...                      ...       ...   
12244  I-Ek plus MCC peptide   2B4 TCR   
12245  I-Ek plus MCC peptide   2B4 TCR   
12246  I-Ek plus MCC peptide   2B4 TCR   
12247  I-Ek plus MCC peptide   2B4 TCR   
12248  I-Ek plus MCC peptide   2B4 TCR   

                                               wild_seq1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12244  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12245  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12246  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12247  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12248  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   

                                               wild_seq2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12244  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12245  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12246  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12247  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12248  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   

                                              mutant_seq  
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...  
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...  
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...  
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...  
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...  
...                                                  ...  
12244                                                NaN  
12245                                                NaN  
12246                                                NaN  
12247                                                NaN  
12248                                                NaN  

[12249 rows x 9 columns]

In [28]:
# check and remove if there's any duplicates
df.drop_duplicates(inplace=True)

In [29]:
df

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12243  3QIB            KP9R          2.4E-04         5.5E-06   
12244  3QIB           TP12A         >1.1E-03         5.5E-06   
12245  3QIB           TP12S         3.38E-05         5.5E-06   
12246  3QIB           TP12N         4.34E-05         5.5E-06   
12247  3QIB      YP7F,TP12S         4.29E-05         5.5E-06   

                   Protein 1 Protein 2  \
0       Subtilisin Carlsberg   Eglin c   
1       Subtilisin Carlsberg   Eglin c   
2       Subtilisin Carlsberg   Eglin c   
3       Subtilisin Carlsberg   Eglin c   
4       Subtilisin Carlsberg   Eglin c   
...                      ...       ...   
12243  I-Ek plus MCC peptide   2B4 TCR   
12244  I-Ek plus MCC peptide   2B4 TCR   
12245  I-Ek plus MCC peptide   2B4 TCR   
12246  I-Ek plus MCC peptide   2B4 TCR   
12247  I-Ek plus MCC peptide   2B4 TCR   

                                               wild_seq1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12243  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12244  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12245  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12246  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   
12247  IKEEHTIIQAEFYLLPDKRGEFMFDFDGDEIFHVDIEKSETIWRLE...   

                                               wild_seq2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12243  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12244  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12245  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12246  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   
12247  GSGGGGSRPWFLEYCKSECHFYNGTQRVRLLVRYFYNLEENLRFDS...   

                                              mutant_seq  
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...  
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...  
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...  
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...  
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...  
...                                                  ...  
12243                                                NaN  
12244                                                NaN  
12245                                                NaN  
12246                                                NaN  
12247                                                NaN  

[9074 rows x 9 columns]

In [6]:
# adjust the columns of wt_seq1 and wt_seq2, so that mutations will consistently apply to wt_seq2
sample_1 = 'TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLDLRYNRVRVFYNPGTNVVNHVPHVG'
sample_2 = 'TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGDLRYNRVRVFYNPGTNVVNHVPHVG'
sample_3 = 'AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVGGASFVAGEAYNTDGNGHGTHVAGTVAALDNTTGVLGVAPSVSLYAVKVLNSSGSGSYSGIVSGIEWATTNGMDVINMSLGGASGSTAMKQAVDNAYARGVVVVAAAGNSGNSGSTNTIGYPAKYDSVIAVGAVDSNSNRASFSSVGAELE'

In [7]:
fuzz.ratio(sample_1, sample_3)

29

In [35]:
df_ = df.copy()
df_.dropna(inplace=True)
df_['wild_seq_1'] = df_['wild_seq1']
df_['wild_seq_2'] = df_['wild_seq2']
df_['Protein_1'] = df_['Protein 1']
df_['Protein_2'] = df_['Protein 2']
#df_ = df_.reindex(columns=df_.columns.values)
df_

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12215  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
12216  2WPT           NA34A         6.49E-07         8.2E-07   
12217  2WPT           SB84A         7.09E-07         8.2E-07   
12218  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
12219  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                         Protein 1         Protein 2  \
0             Subtilisin Carlsberg           Eglin c   
1             Subtilisin Carlsberg           Eglin c   
2             Subtilisin Carlsberg           Eglin c   
3             Subtilisin Carlsberg           Eglin c   
4             Subtilisin Carlsberg           Eglin c   
...                            ...               ...   
12215  Colicin E2 immunity protein  Colicin E9 DNase   
12216  Colicin E2 immunity protein  Colicin E9 DNase   
12217  Colicin E2 immunity protein  Colicin E9 DNase   
12218  Colicin E2 immunity protein  Colicin E9 DNase   
12219  Colicin E2 immunity protein  Colicin E9 DNase   

                                               wild_seq1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12215  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12217  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12218  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                               wild_seq2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                              mutant_seq  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                              wild_seq_1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                        

In [17]:
df_ = df_.iloc[:100]
df_

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0    1CSE           LI45G         5.26E-11        1.12E-12   
1    1CSE           LI45S         8.33E-12        1.12E-12   
2    1CSE           LI45P         1.02E-07        1.12E-12   
3    1CSE           LI45I         1.72E-10        1.12E-12   
4    1CSE           LI45D         1.92E-09        1.12E-12   
..    ...             ...              ...             ...   
100  1IAR           RA85A         3.33E-10        1.62E-10   
101  1IAR           RA85E         1.28E-09        1.62E-10   
102  1IAR           RA88Q         1.92E-08        1.62E-10   
103  1IAR           RA88D              n.b        1.62E-10   
104  1IAR           RA88A         9.16E-08        1.62E-10   

                Protein 1               Protein 2  \
0    Subtilisin Carlsberg                 Eglin c   
1    Subtilisin Carlsberg                 Eglin c   
2    Subtilisin Carlsberg                 Eglin c   
3    Subtilisin Carlsberg                 Eglin c   
4    Subtilisin Carlsberg                 Eglin c   
..                    ...                     ...   
100         Interleukin-4  Interleukin-4 receptor   
101         Interleukin-4  Interleukin-4 receptor   
102         Interleukin-4  Interleukin-4 receptor   
103         Interleukin-4  Interleukin-4 receptor   
104         Interleukin-4  Interleukin-4 receptor   

                                             wild_seq1  \
0    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
..                                                 ...   
100  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
101  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
102  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
103  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
104  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   

                                             wild_seq2  \
0    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
..                                                 ...   
100  FKVLQEPTCVSDYMSISTCEWKMNGPTNCSTELRLLYQLVFLLSEA...   
101  FKVLQEPTCVSDYMSISTCEWKMNGPTNCSTELRLLYQLVFLLSEA...   
102  FKVLQEPTCVSDYMSISTCEWKMNGPTNCSTELRLLYQLVFLLSEA...   
103  FKVLQEPTCVSDYMSISTCEWKMNGPTNCSTELRLLYQLVFLLSEA...   
104  FKVLQEPTCVSDYMSISTCEWKMNGPTNCSTELRLLYQLVFLLSEA...   

                                            mutant_seq  \
0    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4    TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   
..                                                 ...   
100  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
101  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
102  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
103  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
104  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   

                                            wild_seq_1  \
0    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4    AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
..                                                 ...   
100  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
101  HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFC...   
102  HKCDIT

In [36]:
"""
    This chunk should re-organize the dataframe so that:
    1. all the sequence listed in wt_seq2 will have positions mutated
    2. if the wt_seq2 and wt_seq1 flipped, so well columns [Protein1, Protein2]
"""
for index, row in df_.iterrows():
    if fuzz.ratio(row['wild_seq1'], row['mutant_seq']) > fuzz.ratio(row['wild_seq2'], row['mutant_seq']) :
        # then the two sequences are similar
        # flip the sequence 1 to sequence 2
            df_.at[index, 'wild_seq_1'] = row['wild_seq2']
            df_.at[index, 'wild_seq_2'] = row['wild_seq1']
            df_.at[index, 'Protein_1'] = row['Protein 2']
            df_.at[index, 'Protein_2'] = row['Protein 1']
    elif fuzz.ratio(row['wild_seq1'], row['mutant_seq'])  < fuzz.ratio(row['wild_seq2'], row['mutant_seq']) :
        pass
    else:
        print(index, fuzz.ratio(row['wild_seq1'], row['mutant_seq']), fuzz.ratio(row['wild_seq2'], row['mutant_seq']))
        print('mutate both sequences?')
df_

7647 100 100
mutate both sequences?


pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12215  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
12216  2WPT           NA34A         6.49E-07         8.2E-07   
12217  2WPT           SB84A         7.09E-07         8.2E-07   
12218  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
12219  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                         Protein 1         Protein 2  \
0             Subtilisin Carlsberg           Eglin c   
1             Subtilisin Carlsberg           Eglin c   
2             Subtilisin Carlsberg           Eglin c   
3             Subtilisin Carlsberg           Eglin c   
4             Subtilisin Carlsberg           Eglin c   
...                            ...               ...   
12215  Colicin E2 immunity protein  Colicin E9 DNase   
12216  Colicin E2 immunity protein  Colicin E9 DNase   
12217  Colicin E2 immunity protein  Colicin E9 DNase   
12218  Colicin E2 immunity protein  Colicin E9 DNase   
12219  Colicin E2 immunity protein  Colicin E9 DNase   

                                               wild_seq1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12215  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12217  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12218  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                               wild_seq2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                              mutant_seq  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                              wild_seq_1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                        

In [37]:
df_.drop(columns=['Protein 1', 'Protein 2', 'wild_seq1', 'wild_seq2'], inplace=True)
cols = ['pdb', 'Mutation(s)_PDB', 'Affinity_mut (M)', 'Affinity_wt (M)','Protein_1',
        'Protein_2','wild_seq_1','wild_seq_2', 'mutant_seq']
df_ = df_[cols]
df_

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12215  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
12216  2WPT           NA34A         6.49E-07         8.2E-07   
12217  2WPT           SB84A         7.09E-07         8.2E-07   
12218  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
12219  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                         Protein_1                    Protein_2  \
0             Subtilisin Carlsberg                      Eglin c   
1             Subtilisin Carlsberg                      Eglin c   
2             Subtilisin Carlsberg                      Eglin c   
3             Subtilisin Carlsberg                      Eglin c   
4             Subtilisin Carlsberg                      Eglin c   
...                            ...                          ...   
12215  Colicin E2 immunity protein             Colicin E9 DNase   
12216             Colicin E9 DNase  Colicin E2 immunity protein   
12217  Colicin E2 immunity protein             Colicin E9 DNase   
12218  Colicin E2 immunity protein             Colicin E9 DNase   
12219             Colicin E9 DNase  Colicin E2 immunity protein   

                                              wild_seq_1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12215  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12216  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12217  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12218  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12219  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                              wild_seq_2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                              mutant_seq  
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...  
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...  
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...  
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...  
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...  
...                                                  ...  
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...  
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...  
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...  
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...  
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...  

[7187 rows x 9 columns]

In [33]:
seqs_tuples_wt1 = list(set(zip(df_.Protein_1, df_.wild_seq_1)))
print(len(seqs_tuples_wt1))
seqs_tuples_wt1

289


[('Cyclophilin A',
  'MVNPTVFFDIAVDGEPLGRVSFELFADKVPKTAENFRALSTGEKGFGYKGSCFHRIIPGFMCQGGDFTRHNGTGGKSIYGEKFEDENFILKHTGPGILSMANAGPNTNGSQFFICTAKTEWLDGKHVVFGKVKEGMNIVEAMERFGSRNGKTSKKITIADCGQLE'),
 ('STK25',
  'QAMAHLRGFANQHSRVDPEELFTKLDRIGKGSFGEVYKGIDNHTKEVVAIKIIDLEEAEDEIEDIQQEITVLSQCDSPYITRYFGSYLKSTKLWIIMEYLGGGSALDLLKPGPLEETYIATILREILKGLDYLHSERKIHRDIKAANVLLSEQGDVKLAAFGVAGQLTDTQIKRNTFVGTPFWMAPEVIKQSAYDFKADIWSLGITAIELAKGEPPNSDLHPMRVLFLIPKNSPPTLEGQHSKPFKEFVEACLNKDPRFRPTAKELLKHKFITRYTKKTSFLTELIDRYKRWKSE'),
 ('Colicin E2 immunity protein',
  'MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEHPDGSDLIYYPRDDREDSPEGIVKEIKEWRAANGKSGFKQG'),
 ('H-Ras1',
  'MTEYKLVVVGAGGVGKSALTIQLIQNHFVDKYDPTIEDSYRKQVVIDGETCLLDILDTAGQEEYSAMRDQYMRTGEGFLCVFAINNTKSFEDIHQYREQIKRVKDSDDVPMVLVGNKCDLAARTVESRQAQDLARSYGIPYIETSAKTRQGVEDAFYTLVREIRQHK'),
 ('CAR D1 domain',
  'GITTPEEMIEKAKGETAYLPCKFTLSPEDQGPLDIEWLISPADNQKVDQVIILYSGDKIYDDYYPDLKGRVHFTSNDLKSGDASINVTNLQLSDIGTYQCKVKKAPGVANKKIHLVVLVKPSGA'),
 ('b13 fab',
  'QVQLVESGGGVVQPGRSL

In [38]:
# Generate sequence embeddings to the proteins
seqs_wt1 = df_.wild_seq_1.values.tolist()
seqs_wt2 = df_.wild_seq_2.values.tolist()
seqs_mut = df_.mutant_seq.values.tolist()
print(len(seqs_wt1))
print(len(seqs_mut))
seqs_wt1 = set(seqs_wt1)
seqs_wt2 = set(seqs_wt2)
seqs_mut = set(seqs_mut)
print(len(seqs_wt1))
print(len(seqs_wt2))
print(len(seqs_mut))
seqs_mut

7187
7187
266
328
1525


{'GSGAMAQNLDSMLHGTGMKSDSDQKKSENGVTLAPEDTLPFLKCYCSHHCPEDAINNTCIANGHCFTMIEEDDQGETTLTSGCLGLEGSDFQCRDTPIPHQRRSIECCRTNLCNQYLQPTLPPVVIGPFFDGSIR',
 'TQVCTGTDMKLRLPASPETHLDMLRHLYQGCQVVQGNLELTYLPTNASLSFLQDIQEVQGYVLIAHNQVRQVPLQRLRIVRGTQLFEDNYALAVLDNGDPLNNTTPVTGASPGGLRELQLRSLTEILKGGVLIQRNPQLCYQDTILWKDIFHKNNQLALTLIDTNRSRACHPCSPMCKGSRCWGESSEDCQSLTRTVCAGGCARCKGPLPTDCCHEQCAAGCTGPKHSDCLACLHFNHSGICELHCPALVTYNTDTFESMPNPEGRYTFGASCVTACPYNYLSTDVGSCTLVCPLHNQEVTAEDGTQRCEKCSKPCARVCYGLGMEHLREVRAVTSANIQEFAGCKKIFGSLAFLPESFDGDPASNTAPLQPEQLQVFETLEEITGYLYISAWPDSLPDLSVFQNLQVIRGRILHNGAYSLTLQGLGISWLGLRSLRELGSGLALIHHNTHLCFVHTVPWDQLFRNPHQALLHTANRPEDECVGEGLACHQLCARGHCWGPGPTQCVNCSQFLRGQECVEECRVAQGLPREYVNARHCLPCHPECQPQNGSVTCFGPEADQCVACAHYKDPPFCVARCPSGVKPDLSYMPIWKFPDEEGACQPCPIN',
 'MKTEWPELVGKSVEEAKKVILQDKPAAQIIVLPVGTIVTMEYAIDRVRLFVDRLDNIAQVPRVG',
 'AGVMTGAKFTQIQFGMTRQQVLDIAGAENCETGGSFGDSIHCRGHAAGDYYAYATFGFTSAAADAKVDSKSQMKLLAPSAPTLTLAKFNQVTVGMTRAQVLATVGQGSCTTWSEYYPAYPSTAGVTLSLSCFDVDGYSSTGFYRGSAHLWFTDGVLQGKRQWDLV',
 'MAASRRL

In [ ]:
# 289 vs 266
# some of the proteins are mislabeled, they share same sequences, but protein names got mislabeled

In [39]:
seqs_labeled_wt1 = []
count = 0
for seq in seqs_wt1:
    seqs_labeled_wt1.append(tuple((str('seq' + str(count)), seq)))
    count += 1
seqs_labeled_wt1

[('seq0',
  'GITTPEEMIEKAKGETAYLPCKFTLSPEDQGPLDIEWLISPADNQKVDQVIILYSGDKIYDDYYPDLKGRVHFTSNDLKSGDASINVTNLQLSDIGTYQCKVKKAPGVANKKIHLVVLVKPSGA'),
 ('seq1',
  'MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKEFKSFDDFRKAVWEEVSKDPELSKNLNPSNKSSVSKGYSPFTPKNQQVGGRKVYELHHDKPISQGGEVYDMDNIRVTTPKRHIDIHRGK'),
 ('seq2',
  'HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFCRAATVLRQFYSHHEKDTRCLGATAQQFHRHKQLIRFLKRLDRNLWGLAGLNSCPVKEANQSTLENFLERLKTIMREKYSKCSS'),
 ('seq3',
  'MPVANADVVFDFQNYTAKAGDEVTVDVLVDSKNKPISAMDVKFKVDSPLTIEEIDKESLAFNTTVMTNMAILGANFKSLDDKGEPLVPKDGAAVFTLYVNVPANTPDGTYYVGFNGKNEVHKSNDGSQFTVASKNGAITVGTPNEEGLE'),
 ('seq4',
  'HMDPEFQAARLAKALRELGQTGWYWGSMTVNEAKEKLKEAPEGTFLIRDSSHSDYLLTISVKTSAGPTNLRIEYQDGKFRLDSIICVKSKLKQFDSVVHLIDYYVQMCKDKRTGPEAPRNGTVHLYLTKPLYTSAPSLQHLCRLTINKCTGAIWGLPLPTRLKDYLEEYKFQV'),
 ('seq5',
  'MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEHPDGSDLIYYPRDDREDSPEGIVKEIKEWRAANGKSGFKQG'),
 ('seq6',
  'ASEEEKAWLMASRQQLAKETSNFGFSLLRKISMRHDGNMVFSPFGMSLAMTGLMLGATGPTETQIKRGLHLQALKPTKPGLLPSLFKGLR

In [40]:
seqs_labeled_wt2 = []
count = 0
for seq in seqs_wt2:
    seqs_labeled_wt2.append(tuple((str('seq' + str(count)), seq)))
    count += 1
seqs_labeled_mut = []
count = 0
for seq in seqs_mut:
    seqs_labeled_mut.append(tuple((str('seq' + str(count)), seq)))
    count += 1

In [41]:
# Load ESM-2 model
model, alphabet = esm.pretrained.esm2_t33_650M_UR50D()
batch_converter = alphabet.get_batch_converter()
model.eval()  # disables dropout for deterministic results

ESM2(
  (embed_tokens): Embedding(33, 1280, padding_idx=1)
  (layers): ModuleList(
    (0): TransformerLayer(
      (self_attn): MultiheadAttention(
        (k_proj): Linear(in_features=1280, out_features=1280, bias=True)
        (v_proj): Linear(in_features=1280, out_features=1280, bias=True)
        (q_proj): Linear(in_features=1280, out_features=1280, bias=True)
        (out_proj): Linear(in_features=1280, out_features=1280, bias=True)
        (rot_emb): RotaryEmbedding()
      )
      (self_attn_layer_norm): LayerNorm((1280,), eps=1e-05, elementwise_affine=True)
      (fc1): Linear(in_features=1280, out_features=5120, bias=True)
      (fc2): Linear(in_features=5120, out_features=1280, bias=True)
      (final_layer_norm): LayerNorm((1280,), eps=1e-05, elementwise_affine=True)
    )
    (1): TransformerLayer(
      (self_attn): MultiheadAttention(
        (k_proj): Linear(in_features=1280, out_features=1280, bias=True)
        (v_proj): Linear(in_features=1280, out_features=1280, bia

In [42]:
# find longest sequence
len(max(list(zip(*seqs_labeled_wt1))[1], key=len))

1295

In [43]:
# alternative way to generate batches
from torch.utils.data import TensorDataset
from esm import Alphabet, FastaBatchedDataset
batch_size = 1000
dataset = FastaBatchedDataset(list(zip(*seqs_labeled_wt1))[0], list(zip(*seqs_labeled_wt1))[1])
batches = dataset.get_batch_indices(batch_size, extra_toks_per_seq=1)
data_loader = torch.utils.data.DataLoader(dataset, collate_fn=Alphabet.from_architecture("roberta_large").get_batch_converter(),
            batch_sampler=batches, pin_memory=True)
dataset_seq2 = FastaBatchedDataset(list(zip(*seqs_labeled_wt2))[0], list(zip(*seqs_labeled_wt2))[1])
batches_seq2 = dataset_seq2.get_batch_indices(batch_size, extra_toks_per_seq=1)
data_loader_seq2 = torch.utils.data.DataLoader(dataset_seq2, collate_fn=Alphabet.from_architecture("roberta_large").get_batch_converter(),
            batch_sampler=batches_seq2, pin_memory=True)
dataset_mut = FastaBatchedDataset(list(zip(*seqs_labeled_mut))[0], list(zip(*seqs_labeled_mut))[1])
batches_mut = dataset_mut.get_batch_indices(batch_size, extra_toks_per_seq=1)
data_loader_mut = torch.utils.data.DataLoader(dataset_mut, collate_fn=Alphabet.from_architecture("roberta_large").get_batch_converter(),
            batch_sampler=batches_mut, pin_memory=True)

In [44]:
torch.cuda.empty_cache()

In [45]:
if torch.cuda.is_available():
    model = model.cuda()
    print('Transferred model to GPU')

Transferred model to GPU


In [46]:
list(data_loader.dataset)

[('seq0',
  'GITTPEEMIEKAKGETAYLPCKFTLSPEDQGPLDIEWLISPADNQKVDQVIILYSGDKIYDDYYPDLKGRVHFTSNDLKSGDASINVTNLQLSDIGTYQCKVKKAPGVANKKIHLVVLVKPSGA'),
 ('seq1',
  'MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKEFKSFDDFRKAVWEEVSKDPELSKNLNPSNKSSVSKGYSPFTPKNQQVGGRKVYELHHDKPISQGGEVYDMDNIRVTTPKRHIDIHRGK'),
 ('seq2',
  'HKCDITLQEIIKTLNSLTEQKTLCTELTVTDIFAASKNTTEKETFCRAATVLRQFYSHHEKDTRCLGATAQQFHRHKQLIRFLKRLDRNLWGLAGLNSCPVKEANQSTLENFLERLKTIMREKYSKCSS'),
 ('seq3',
  'MPVANADVVFDFQNYTAKAGDEVTVDVLVDSKNKPISAMDVKFKVDSPLTIEEIDKESLAFNTTVMTNMAILGANFKSLDDKGEPLVPKDGAAVFTLYVNVPANTPDGTYYVGFNGKNEVHKSNDGSQFTVASKNGAITVGTPNEEGLE'),
 ('seq4',
  'HMDPEFQAARLAKALRELGQTGWYWGSMTVNEAKEKLKEAPEGTFLIRDSSHSDYLLTISVKTSAGPTNLRIEYQDGKFRLDSIICVKSKLKQFDSVVHLIDYYVQMCKDKRTGPEAPRNGTVHLYLTKPLYTSAPSLQHLCRLTINKCTGAIWGLPLPTRLKDYLEEYKFQV'),
 ('seq5',
  'MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEHPDGSDLIYYPRDDREDSPEGIVKEIKEWRAANGKSGFKQG'),
 ('seq6',
  'ASEEEKAWLMASRQQLAKETSNFGFSLLRKISMRHDGNMVFSPFGMSLAMTGLMLGATGPTETQIKRGLHLQALKPTKPGLLPSLFKGLR

In [47]:
for batch_idx, (labels, strs, toks) in enumerate(data_loader):
    try:
        print(batch_idx,labels)
    except KeyError:
        print(batch_idx)

0 ['seq100', 'seq178', 'seq134', 'seq81', 'seq203', 'seq9', 'seq181', 'seq77', 'seq66', 'seq235', 'seq179', 'seq35', 'seq143', 'seq29', 'seq97', 'seq170']
1 ['seq222', 'seq136', 'seq12', 'seq126', 'seq133', 'seq112', 'seq187', 'seq109', 'seq131', 'seq169', 'seq14', 'seq211']
2 ['seq26', 'seq256', 'seq56', 'seq25', 'seq68', 'seq251', 'seq74', 'seq132', 'seq44', 'seq226', 'seq5']
3 ['seq218', 'seq104', 'seq174', 'seq28', 'seq36', 'seq147', 'seq153', 'seq54', 'seq118', 'seq192']
4 ['seq91', 'seq225', 'seq196', 'seq197', 'seq30', 'seq45', 'seq138', 'seq230', 'seq18']
5 ['seq158', 'seq216', 'seq232', 'seq60', 'seq164', 'seq257', 'seq129', 'seq228']
6 ['seq13', 'seq208', 'seq61', 'seq102', 'seq252', 'seq38', 'seq105', 'seq107']
7 ['seq94', 'seq0', 'seq173', 'seq249', 'seq188', 'seq202', 'seq2']
8 ['seq83', 'seq159', 'seq144', 'seq17', 'seq1', 'seq96', 'seq215']
9 ['seq240', 'seq253', 'seq103', 'seq237', 'seq78', 'seq151', 'seq201']
10 ['seq236', 'seq234', 'seq130', 'seq160', 'seq20', 'seq186

In [89]:
a = np.array([[[1,2,3],
               [4,5,6],
               [7,8,9],
              [10,11,12]],
              [[7,8,9],
              [10,11,12],
               [7,8,9],
              [10,11,12]]])
np.shape(a)

(2, 4, 3)

In [54]:
a

array([[[ 1,  2,  3],
        [ 4,  5,  6],
        [ 7,  8,  9],
        [10, 11, 12]],

       [[ 7,  8,  9],
        [10, 11, 12],
        [ 7,  8,  9],
        [10, 11, 12]]])

In [57]:
a[1, 1:-1]

array([[10, 11, 12],
       [ 7,  8,  9]])

In [48]:
representation_store_dict = {}
for batch_idx, (labels, strs, toks) in enumerate(data_loader):
    if torch.cuda.is_available():
        toks = toks.to(device='cuda', non_blocking=True)
    with torch.no_grad():
        results = model(toks, repr_layers = [33], return_contacts = True)['representations'][33]
        #results = model(toks, repr_layers = [33], return_contacts = True)['logits']
    print(results.shape)
    results_cpu = results.to(device='cpu')
    for i, str_ in enumerate(strs):
        #if str not in representation_store_dict:
            #representation_store_dict[str] = []
        # only select representations relate to the sequence
        # rest of the sequences are paddings, check notebook
        # create dictionary {sequence: embeddings}
        representation_store_dict[str_] = results_cpu[i, 1: (len(strs[i])+1)].numpy()

torch.Size([16, 60, 1280])
torch.Size([12, 77, 1280])
torch.Size([11, 88, 1280])
torch.Size([10, 98, 1280])
torch.Size([9, 112, 1280])
torch.Size([8, 116, 1280])
torch.Size([8, 124, 1280])
torch.Size([7, 131, 1280])
torch.Size([7, 136, 1280])
torch.Size([7, 138, 1280])
torch.Size([6, 150, 1280])
torch.Size([6, 160, 1280])
torch.Size([6, 167, 1280])
torch.Size([5, 168, 1280])
torch.Size([5, 172, 1280])
torch.Size([5, 180, 1280])
torch.Size([5, 187, 1280])
torch.Size([5, 199, 1280])
torch.Size([4, 208, 1280])
torch.Size([4, 212, 1280])
torch.Size([4, 213, 1280])
torch.Size([4, 216, 1280])
torch.Size([4, 216, 1280])
torch.Size([4, 218, 1280])
torch.Size([4, 221, 1280])
torch.Size([4, 226, 1280])
torch.Size([4, 233, 1280])
torch.Size([4, 241, 1280])
torch.Size([4, 243, 1280])
torch.Size([4, 250, 1280])
torch.Size([3, 264, 1280])
torch.Size([3, 265, 1280])
torch.Size([3, 267, 1280])
torch.Size([3, 274, 1280])
torch.Size([3, 276, 1280])
torch.Size([3, 283, 1280])
torch.Size([3, 284, 1280])
t

In [115]:
representation_store_dict

{'ARTKQTARKS': array([[ 0.02447946,  0.01928901, -0.03956539, ...,  0.12661682,
         -0.09285621,  0.01617499],
        [ 0.10751038,  0.06919377,  0.12876596, ..., -0.00814786,
          0.02145161, -0.02784804],
        [ 0.00273106,  0.03329812,  0.06105419, ...,  0.07983748,
         -0.03923513, -0.00519595],
        ...,
        [ 0.07251852,  0.07814158,  0.15600905, ...,  0.02425219,
          0.00744778, -0.06048933],
        [-0.06360918,  0.06384679,  0.1498925 , ..., -0.01001437,
         -0.13084146,  0.01428795],
        [ 0.07733045,  0.06695724,  0.13977003, ...,  0.08957948,
         -0.2533254 ,  0.00227757]], dtype=float32),
 'YMDFDDDIPF': array([[ 0.13910443, -0.07379941, -0.29339817, ...,  0.00111225,
         -0.07300624, -0.07609034],
        [ 0.05488537, -0.12718895, -0.0194888 , ...,  0.01878373,
         -0.191497  ,  0.02732703],
        [ 0.06376954, -0.13735689, -0.09811898, ..., -0.12271725,
          0.07584549,  0.06119155],
        ...,
        [ 0

In [119]:
df_

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12215  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
12216  2WPT           NA34A         6.49E-07         8.2E-07   
12217  2WPT           SB84A         7.09E-07         8.2E-07   
12218  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
12219  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                         Protein_1                    Protein_2  \
0             Subtilisin Carlsberg                      Eglin c   
1             Subtilisin Carlsberg                      Eglin c   
2             Subtilisin Carlsberg                      Eglin c   
3             Subtilisin Carlsberg                      Eglin c   
4             Subtilisin Carlsberg                      Eglin c   
...                            ...                          ...   
12215  Colicin E2 immunity protein             Colicin E9 DNase   
12216             Colicin E9 DNase  Colicin E2 immunity protein   
12217  Colicin E2 immunity protein             Colicin E9 DNase   
12218  Colicin E2 immunity protein             Colicin E9 DNase   
12219             Colicin E9 DNase  Colicin E2 immunity protein   

                                              wild_seq_1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12215  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12216  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12217  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12218  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12219  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                              wild_seq_2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                              mutant_seq  
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...  
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...  
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...  
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...  
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...  
...                                                  ...  
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...  
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...  
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...  
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...  
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...  

[7187 rows x 9 columns]

In [93]:
seqs_labeled_wt1

[('seq0',
  'RSSNELHQVPSNCDCLNGGTCVSNKYFSNIHWCNCPKKFGGQHCEIDKSKTCYEGNGHFYRGKASTDTMGRPCLPWNSATVLQQTYHAHRSDALQLGLGKHNYCRNPDNRRRPWCYVQVGLKPLVQECMVHDCAD'),
 ('seq1', 'ALGLLAPLRETKSTNPASRVMEMEPETMETKSVIDSRV'),
 ('seq2',
  'THTCPPCPAPELLGGPSVFLFPPKPKDTLMISRTPEVTCVVVDVSHEDPQVKFNWYVDGVQVHNAKTKPREQQYNSTYRVVSVLTVLHQNWLDGKEYKCKVSNKALPAPIEKTISKAKGQPREPQVYTLPPSREEMTKNQVSLTCLVKGFYPSDIAVEWESNGQPENNYKTTPPVLDSDGSFFLYSKLTVDKSRWQQGNVFSCSVMHEALHNHYTQKSLSLSPG'),
 ('seq3',
  'MLSGVWFLSVLTVAGILQTESRKTAKDICKIRCLCEEKENVLNINCENKGFTTVSLLQPPQYRIYQLFLNGNLLTRLYPNEFVNYSNAVTLHLGNNGLQEIRPGAFSGLKTLKRLHLNNNKLEVLREDTFLGLESLEYLQADYNYISTIEAGAFSKLNKLKVLILNDNLLLSLPSNVFRFVLLTHLDLRGNRLKVMPFAGVLEHIGGIMEIQLEENPWNCTCDLLPLKAWLDTITVFVGEIVCETPFRLHGKDVTQLTRQDLCPRKHHHHHH'),
 ('seq4',
  'MDRRQKRLIFSTITSKMNLSEEVDLEDYVARPDKISGADINSICQESGMLAVRENRYIVLAKDFEKAYKTVIKKDEQEHEFYK'),
 ('seq5',
  'APLAHCDGRGGLKLSQDMDTCEDILPCVPFSVAKSVKSLYLGRMFSGTPVIRLRFKRLQPTRLVAEFDFRTFDPEGILLFAGGHQDSTWIVLALRAGRLELQLRYNGVGRVTSSGPVINHGMWQTISVEELARNLVIKVNRDAVMKIAVAGD

In [49]:
# take the average of the representations of the proteins
# for umaps, along axis 0
sequence_embeddings = {key: np.mean(value, axis=0, keepdims=True) for key, value in representation_store_dict.items()}
#print({key: value.shape for key, value in sequence_embeddings.items()})
sequence_embeddings

{'YMDFDDDIPF': array([[ 0.04857468, -0.00012262, -0.10690913, ..., -0.11258976,
         -0.04252142,  0.07379431]], dtype=float32),
 'ARTKQTARKS': array([[ 0.0223621 ,  0.06744134,  0.06751989, ...,  0.0498579 ,
         -0.09143854,  0.00964986]], dtype=float32),
 'CGVPAIQPVLSGL': array([[ 0.00409246,  0.07187316,  0.08544851, ..., -0.01148665,
         -0.04319402,  0.05069447]], dtype=float32),
 'AVPIAQKSEPHSLSS': array([[ 0.01182264,  0.13893493,  0.05097224, ..., -0.09801121,
         -0.09132418, -0.00897526]], dtype=float32),
 'ARTKQTARKSTGGKA': array([[-0.03295551,  0.05737768, -0.0015403 , ...,  0.09619958,
         -0.08495762,  0.02021424]], dtype=float32),
 'ARTKQTARKSTGGKAY': array([[-0.05625677,  0.04186503,  0.03291382, ...,  0.09167849,
         -0.06138652,  0.02887965]], dtype=float32),
 'KEPDYLDIPAFLRKQAD': array([[ 0.02545632,  0.01806677, -0.04201803, ..., -0.09341508,
         -0.05944117, -0.04591647]], dtype=float32),
 'XRRRRCPLYISYDPVCRRRRX': array([[-0.015403

In [50]:
representation_store_dict_seq2 = {}
for batch_idx, (labels, strs, toks) in enumerate(data_loader_seq2):
    if torch.cuda.is_available():
        toks = toks.to(device='cuda', non_blocking=True)
    with torch.no_grad():
        results = model(toks, repr_layers = [33], return_contacts = True)['representations'][33]
        #results = model(toks, repr_layers = [33], return_contacts = True)['logits']
    results_cpu = results.to(device='cpu')
    for i, str_ in enumerate(strs):
        #if str not in representation_store_dict:
            #representation_store_dict[str] = []
        # only select representations relate to the sequence
        # rest of the sequences are paddings, check notebook
        # create dictionary {sequence: embeddings}
        representation_store_dict_seq2[str_] = results_cpu[i, 1: (len(strs[i])+1)].numpy()
sequence_embeddings_seq2 = {key: np.mean(value, axis=0, keepdims=True) for key, value in representation_store_dict_seq2.items()}
representation_store_dict_mut = {}
for batch_idx, (labels, strs, toks) in enumerate(data_loader_mut):
    if torch.cuda.is_available():
        toks = toks.to(device='cuda', non_blocking=True)
    with torch.no_grad():
        results = model(toks, repr_layers = [33], return_contacts = True)['representations'][33]
        #results = model(toks, repr_layers = [33], return_contacts = True)['logits']
    results_cpu = results.to(device='cpu')
    for i, str_ in enumerate(strs):
        #if str not in representation_store_dict:
            #representation_store_dict[str] = []
        # only select representations relate to the sequence
        # rest of the sequences are paddings, check notebook
        # create dictionary {sequence: embeddings}
        representation_store_dict_mut[str_] = results_cpu[i, 1: (len(strs[i])+1)].numpy()
sequence_embeddings_mut = {key: np.mean(value, axis=0, keepdims=True) for key, value in representation_store_dict_mut.items()}


torch.Size([19, 53, 1280])
torch.Size([16, 60, 1280])
torch.Size([16, 63, 1280])
torch.Size([15, 67, 1280])
torch.Size([13, 75, 1280])
torch.Size([12, 84, 1280])
torch.Size([10, 92, 1280])
torch.Size([9, 109, 1280])
torch.Size([9, 112, 1280])
torch.Size([8, 123, 1280])
torch.Size([7, 130, 1280])
torch.Size([7, 135, 1280])
torch.Size([7, 136, 1280])
torch.Size([7, 138, 1280])
torch.Size([7, 142, 1280])
torch.Size([6, 148, 1280])
torch.Size([6, 167, 1280])
torch.Size([5, 168, 1280])
torch.Size([5, 169, 1280])
torch.Size([5, 179, 1280])
torch.Size([5, 187, 1280])
torch.Size([5, 188, 1280])
torch.Size([5, 193, 1280])
torch.Size([5, 197, 1280])
torch.Size([4, 201, 1280])
torch.Size([4, 211, 1280])
torch.Size([4, 212, 1280])
torch.Size([4, 216, 1280])
torch.Size([4, 216, 1280])
torch.Size([4, 217, 1280])
torch.Size([4, 221, 1280])
torch.Size([4, 223, 1280])
torch.Size([4, 233, 1280])
torch.Size([4, 233, 1280])
torch.Size([4, 241, 1280])
torch.Size([4, 243, 1280])
torch.Size([3, 264, 1280])
t

In [53]:
def update_embeddings(row, embedding_dict):
    """
    add embeddings to the metadata column.
    cannot do the reverse, because due to mislabel, several different protein names share the same sequences
    but as long as sequences are correct, so will the embeddings
    """
    for key, value in embedding_dict.items():
        if row == key:
            return value
df_['wild_seq_1_embeddings'] = df_['wild_seq_1'].apply(update_embeddings, embedding_dict=sequence_embeddings)
df_['wild_seq_2_embeddings'] = df_['wild_seq_2'].apply(update_embeddings, embedding_dict=sequence_embeddings_seq2)
df_['mutant_seq_embeddings'] = df_['mutant_seq'].apply(update_embeddings, embedding_dict=sequence_embeddings_mut)
df_

/var/tmp/pbs.784522.hn-10-03/ipykernel_254365/11333128.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_['wild_seq_1_embeddings'] = df_['wild_seq_1'].apply(update_embeddings, embedding_dict=sequence_embeddings)
/var/tmp/pbs.784522.hn-10-03/ipykernel_254365/11333128.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_['wild_seq_2_embeddings'] = df_['wild_seq_2'].apply(update_embeddings, embedding_dict=sequence_embeddings_seq2)
/var/tmp/pbs.784522.hn-10-03/ipykernel_254365/11333128.py:12: SettingWi

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12215  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
12216  2WPT           NA34A         6.49E-07         8.2E-07   
12217  2WPT           SB84A         7.09E-07         8.2E-07   
12218  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
12219  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                         Protein_1                    Protein_2  \
0             Subtilisin Carlsberg                      Eglin c   
1             Subtilisin Carlsberg                      Eglin c   
2             Subtilisin Carlsberg                      Eglin c   
3             Subtilisin Carlsberg                      Eglin c   
4             Subtilisin Carlsberg                      Eglin c   
...                            ...                          ...   
12215  Colicin E2 immunity protein             Colicin E9 DNase   
12216             Colicin E9 DNase  Colicin E2 immunity protein   
12217  Colicin E2 immunity protein             Colicin E9 DNase   
12218  Colicin E2 immunity protein             Colicin E9 DNase   
12219             Colicin E9 DNase  Colicin E2 immunity protein   

                                              wild_seq_1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12215  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12216  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12217  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12218  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12219  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                              wild_seq_2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                              mutant_seq  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                   wild_seq_1_embeddings  \
0      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
1      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
2      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
3      [[-0.03217955, -0.156769

In [54]:
df_.to_csv('proteins_embeddings_meta.csv', index=False)

In [ ]:
# extract meta information to draw umaps

In [55]:
from umap import UMAP
import plotly.express as px

In [150]:
ppi = df_['Protein_1']+'___'+df_['Protein_2']
ppi

0                        Subtilisin Carlsberg___Eglin c
1                        Subtilisin Carlsberg___Eglin c
2                        Subtilisin Carlsberg___Eglin c
3                        Subtilisin Carlsberg___Eglin c
4                        Subtilisin Carlsberg___Eglin c
                              ...                      
12215    Colicin E2 immunity protein___Colicin E9 DNase
12216    Colicin E9 DNase___Colicin E2 immunity protein
12217    Colicin E2 immunity protein___Colicin E9 DNase
12218    Colicin E2 immunity protein___Colicin E9 DNase
12219    Colicin E9 DNase___Colicin E2 immunity protein
Length: 7187, dtype: object

In [193]:
prot_1 = df_['Protein_1']
prot_2 = df_['Protein_2']
prot_mut = df_['Protein_2']+'_'+'mut'
seq_1 = df_['wild_seq_1']
seq_2 = df_['wild_seq_2']
seq_mut = df_['mutant_seq']
embed_1 = df_['wild_seq_1_embeddings']
embed_2 = df_['wild_seq_2_embeddings']
embed_mut = df_['mutant_seq_embeddings']
affinity_wt = df_['Affinity_wt (M)']
affinity_mut = df_['Affinity_mut (M)']
label_wt_1 = pd.Series(['wt1']*len(prot_1))
label_wt_2 = pd.Series(['wt2']*len(prot_2))
label_mut = pd.Series(['mut']*len(prot_mut))
pdbs = df_['pdb']
mut = df_['Mutation(s)_PDB']
mut_status_wt = pd.Series([np.nan]*len(prot_1))

In [194]:
df_meta = pd.DataFrame({
    'PDB': pd.concat([pdbs, pdbs, pdbs], ignore_index=True),
    'Protein': pd.concat([prot_1, prot_2, prot_mut], ignore_index=True),
    'Mutation': pd.concat([mut_status_wt, mut_status_wt, mut], ignore_index=True),
    'Sequence': pd.concat([seq_1, seq_2, seq_mut], ignore_index=True),
    'PPI': pd.concat([ppi, ppi, ppi], ignore_index=True),
    'Label': pd.concat([label_wt_1, label_wt_2, label_mut], ignore_index=True),
    'Affinity': pd.concat([affinity_wt, affinity_mut, affinity_mut], ignore_index=True),
    'Embedding': pd.concat([embed_1, embed_2, embed_mut], ignore_index=True),
})
df_meta

PDB                          Protein     Mutation  \
0      1CSE             Subtilisin Carlsberg          NaN   
1      1CSE             Subtilisin Carlsberg          NaN   
2      1CSE             Subtilisin Carlsberg          NaN   
3      1CSE             Subtilisin Carlsberg          NaN   
4      1CSE             Subtilisin Carlsberg          NaN   
...     ...                              ...          ...   
21556  2WPT             Colicin E9 DNase_mut  DA33A,FB86A   
21557  2WPT  Colicin E2 immunity protein_mut        NA34A   
21558  2WPT             Colicin E9 DNase_mut        SB84A   
21559  2WPT             Colicin E9 DNase_mut  SB84A,NA34A   
21560  2WPT  Colicin E2 immunity protein_mut  SB84A,NA34A   

                                                Sequence  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
21556  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
21557  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
21558  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
21559  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
21560  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                                  PPI Label  Affinity  \
0                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
1                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
2                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
3                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
4                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
...                                               ...   ...       ...   
21556  Colicin E2 immunity protein___Colicin E9 DNase   mut  6.21E-07   
21557  Colicin E9 DNase___Colicin E2 immunity protein   mut  6.49E-07   
21558  Colicin E2 immunity protein___Colicin E9 DNase   mut  7.09E-07   
21559  Colicin E2 immunity protein___Colicin E9 DNase   mut  3.92E-07   
21560  Colicin E9 DNase___Colicin E2 immunity protein   mut  3.92E-07   

                                               Embedding  
0      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...  
1      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...  
2      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...  
3      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...  
4      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...  
...                                                  ...  
21556  [[-0.02314554, -0.030065024, -0.04236627, 0.00...  
21557  [[0.040997185, 0.060716324, 0.011485457, 0.042...  
21558  [[-0.024812423, -0.03491652, -0.039183006, 0.0...  
21559  [[-0.024812423, -0.03491652, -0.039183006, 0.0...  
21560  [[0.040997185, 0.060716324, 0.011485457, 0.042...  

[21561 rows x 8 columns]

In [202]:
expanded_embeddings = df_meta['Embedding'].apply(lambda x: pd.Series(x[0]))
df_umap = pd.concat([df_meta, expanded_embeddings], axis=1)
df_umap.drop(['Embedding'], axis=1, inplace=True)
df_umap

PDB                          Protein     Mutation  \
0      1CSE             Subtilisin Carlsberg          NaN   
1      1CSE             Subtilisin Carlsberg          NaN   
2      1CSE             Subtilisin Carlsberg          NaN   
3      1CSE             Subtilisin Carlsberg          NaN   
4      1CSE             Subtilisin Carlsberg          NaN   
...     ...                              ...          ...   
21556  2WPT             Colicin E9 DNase_mut  DA33A,FB86A   
21557  2WPT  Colicin E2 immunity protein_mut        NA34A   
21558  2WPT             Colicin E9 DNase_mut        SB84A   
21559  2WPT             Colicin E9 DNase_mut  SB84A,NA34A   
21560  2WPT  Colicin E2 immunity protein_mut  SB84A,NA34A   

                                                Sequence  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
21556  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
21557  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
21558  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
21559  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
21560  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                                  PPI Label  Affinity  \
0                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
1                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
2                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
3                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
4                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
...                                               ...   ...       ...   
21556  Colicin E2 immunity protein___Colicin E9 DNase   mut  6.21E-07   
21557  Colicin E9 DNase___Colicin E2 immunity protein   mut  6.49E-07   
21558  Colicin E2 immunity protein___Colicin E9 DNase   mut  7.09E-07   
21559  Colicin E2 immunity protein___Colicin E9 DNase   mut  3.92E-07   
21560  Colicin E9 DNase___Colicin E2 immunity protein   mut  3.92E-07   

              0         1         2  ...      1270      1271      1272  \
0     -0.032180 -0.156770 -0.000691  ... -0.009642 -0.058612  0.030370   
1     -0.032180 -0.156770 -0.000691  ... -0.009642 -0.058612  0.030370   
2     -0.032180 -0.156770 -0.000691  ... -0.009642 -0.058612  0.030370   
3     -0.032180 -0.156770 -0.000691  ... -0.009642 -0.058612  0.030370   
4     -0.032180 -0.156770 -0.000691  ... -0.009642 -0.058612  0.030370   
...         ...       ...       ...  ...       ...       ...       ...   
21556 -0.023146 -0.030065 -0.042366  ...  0.028587 -0.030711  0.028562   
21557  0.040997  0.060716  0.011485  ...  0.061316 -0.110644 -0.032557   
21558 -0.024812 -0.034917 -0.039183  ...  0.032775 -0.029655  0.027244   
21559 -0.024812 -0.034917 -0.039183  ...  0.032775 -0.029655  0.027244   
21560  0.040997  0.060716  0.011485  ...  0.061316 -0.110644 -0.032557   

           1273      1274      1275      1276      1277      1278      1279  
0      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
1      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
2      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
3      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
4      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
...         ...       ...       ...       ...       ...       ...       ...  
21556  0.041031  0.036093  0.043161  0.159644 -0.032207  0.014414  0.100678  
21557  0.077818  0.002379  0.042844  0.068300 -0.051918 -0.032073  0.005497  
21558  0.041603  0.035866  0.041392  0.160559 -0.034255  0.013175  0.098460  
21559  0

In [119]:
# alternative ways of extracting embeddings
#sequences = df_[['wild_seq_1', 'wild_seq_2', 'mutant_seq']].melt(value_name='sequences').drop(columns='variable')
#embeddings = df_[['wild_seq_1_embeddings', 'wild_seq_2_embeddings', 'mutant_seq_embeddings']].melt(value_name='embeddings').drop(columns='variable')
#df_sequences = pd.DataFrame({
#    'sequences': sequences['sequences'],
#})
#expanded_embeddings = embeddings['embeddings'].apply(lambda x: pd.Series(x[0]))
#df_umap = pd.concat([df_sequences, expanded_embeddings], axis=1)
#df_umap

sequences         0         1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG... -0.032180 -0.156770   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG... -0.032180 -0.156770   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG... -0.032180 -0.156770   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG... -0.032180 -0.156770   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG... -0.032180 -0.156770   
...                                                  ...       ...       ...   
21556  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE... -0.023146 -0.030065   
21557  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...  0.040997  0.060716   
21558  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE... -0.024812 -0.034917   
21559  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE... -0.024812 -0.034917   
21560  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...  0.040997  0.060716   

              2         3         4         5         6         7         8  \
0     -0.000691  0.196635 -0.085537  0.036425  0.051999 -0.278995 -0.031392   
1     -0.000691  0.196635 -0.085537  0.036425  0.051999 -0.278995 -0.031392   
2     -0.000691  0.196635 -0.085537  0.036425  0.051999 -0.278995 -0.031392   
3     -0.000691  0.196635 -0.085537  0.036425  0.051999 -0.278995 -0.031392   
4     -0.000691  0.196635 -0.085537  0.036425  0.051999 -0.278995 -0.031392   
...         ...       ...       ...       ...       ...       ...       ...   
21556 -0.042366  0.004902 -0.033540 -0.052219  0.021217 -0.160497  0.014909   
21557  0.011485  0.042063 -0.066023  0.053417 -0.009934  0.040825  0.072982   
21558 -0.039183  0.003409 -0.034276 -0.050773  0.022653 -0.158220  0.015947   
21559 -0.039183  0.003409 -0.034276 -0.050773  0.022653 -0.158220  0.015947   
21560  0.011485  0.042063 -0.066023  0.053417 -0.009934  0.040825  0.072982   

       ...      1270      1271      1272      1273      1274      1275  \
0      ... -0.009642 -0.058612  0.030370  0.026104 -0.016590 -0.103824   
1      ... -0.009642 -0.058612  0.030370  0.026104 -0.016590 -0.103824   
2      ... -0.009642 -0.058612  0.030370  0.026104 -0.016590 -0.103824   
3      ... -0.009642 -0.058612  0.030370  0.026104 -0.016590 -0.103824   
4      ... -0.009642 -0.058612  0.030370  0.026104 -0.016590 -0.103824   
...    ...       ...       ...       ...       ...       ...       ...   
21556  ...  0.028587 -0.030711  0.028562  0.041031  0.036093  0.043161   
21557  ...  0.061316 -0.110644 -0.032557  0.077818  0.002379  0.042844   
21558  ...  0.032775 -0.029655  0.027244  0.041603  0.035866  0.041392   
21559  ...  0.032775 -0.029655  0.027244  0.041603  0.035866  0.041392   
21560  ...  0.061316 -0.110644 -0.032557  0.077818  0.002379  0.042844   

           1276      1277      1278      1279  
0      0.098748 -0.207159 -0.001669  0.071841  
1      0.098748 -0.207159 -0.001669  0.071841  
2      0.098748 -0.207159 -0.001669  0.071841  
3      0.098748 -0.207159 -0.001669  0.071841  
4      0.098748 -0.207159 -0.001669  0.071841  
...         ...       ...       ...       ...  
21556  0.159644 -0.032207  0.014414  0.100678  
21557  0.068300 -0.051918 -0.032073  0.005497  
21558  0.160559 -0.034255  0.013175  0.098460  
21559  0.160559 -0.034255  0.013175  0.098460  
21560  0.068300 -0.051918 -0.032073  0.005497  

[21561 rows x 1281 columns]

In [203]:
df_umap.drop_duplicates(inplace=True, ignore_index=True)
# weird duplicates should be dropped under the affinity column
# keep the first encounter first
# seems like a lot of wts mistakenly have affinities of mutants
#df_umap= df_umap.drop_duplicates(subset='Affinity', keep='first', ignore_index=True)
df_umap

PDB                          Protein     Mutation  \
0      1CSE             Subtilisin Carlsberg          NaN   
1      1ACB        Bovine alpha-chymotrypsin          NaN   
2      1SBN                   Subtilisin BPN          NaN   
3      1SIB                   Subtilisin BPN          NaN   
4      1TM1                   Subtilisin BPN          NaN   
...     ...                              ...          ...   
12318  2WPT             Colicin E9 DNase_mut  DA33A,FB86A   
12319  2WPT  Colicin E2 immunity protein_mut        NA34A   
12320  2WPT             Colicin E9 DNase_mut        SB84A   
12321  2WPT             Colicin E9 DNase_mut  SB84A,NA34A   
12322  2WPT  Colicin E2 immunity protein_mut  SB84A,NA34A   

                                                Sequence  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      CGVPAIQPVLSGLSRIVNGEEAVPGSWPWQVSLQDKTGFHFCGGSL...   
2      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
3      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
4      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
...                                                  ...   
12318  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12319  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12320  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12321  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12322  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                                  PPI Label  Affinity  \
0                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
1                 Bovine alpha-chymotrypsin___Eglin c   wt1  1.49E-12   
2                            Subtilisin BPN___Eglin c   wt1   5.4E-11   
3                            Subtilisin BPN___Eglin c   wt1   1.1E-10   
4           Subtilisin BPN___Chymotrypsin inhibitor 2   wt1     2E-12   
...                                               ...   ...       ...   
12318  Colicin E2 immunity protein___Colicin E9 DNase   mut  6.21E-07   
12319  Colicin E9 DNase___Colicin E2 immunity protein   mut  6.49E-07   
12320  Colicin E2 immunity protein___Colicin E9 DNase   mut  7.09E-07   
12321  Colicin E2 immunity protein___Colicin E9 DNase   mut  3.92E-07   
12322  Colicin E9 DNase___Colicin E2 immunity protein   mut  3.92E-07   

              0         1         2  ...      1270      1271      1272  \
0     -0.032180 -0.156770 -0.000691  ... -0.009642 -0.058612  0.030370   
1     -0.024063 -0.075022  0.095781  ... -0.030885 -0.010721  0.019142   
2     -0.026634 -0.127109 -0.023703  ... -0.008960 -0.038177  0.030544   
3     -0.026634 -0.127109 -0.023703  ... -0.008960 -0.038177  0.030544   
4     -0.024246 -0.125899 -0.015986  ... -0.013187 -0.044538  0.007275   
...         ...       ...       ...  ...       ...       ...       ...   
12318 -0.023146 -0.030065 -0.042366  ...  0.028587 -0.030711  0.028562   
12319  0.040997  0.060716  0.011485  ...  0.061316 -0.110644 -0.032557   
12320 -0.024812 -0.034917 -0.039183  ...  0.032775 -0.029655  0.027244   
12321 -0.024812 -0.034917 -0.039183  ...  0.032775 -0.029655  0.027244   
12322  0.040997  0.060716  0.011485  ...  0.061316 -0.110644 -0.032557   

           1273      1274      1275      1276      1277      1278      1279  
0      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
1      0.011965 -0.024791 -0.073087  0.157850 -0.125122  0.007609  0.012032  
2     -0.026940 -0.018413 -0.092624  0.065720 -0.223058 -0.021946  0.083181  
3     -0.026940 -0.018413 -0.092624  0.065720 -0.223058 -0.021946  0.083181  
4      0.000478 -0.014124 -0.083644  0.048960 -0.228387 -0.020252  0.054023  
...         ...       ...       ...       ...       ...       ...       ...  
12318  0.041031  0.036093  0.043161  0.159644 -0.032207  0.014414  0.100678  
12319  0.077818  0.002379  0.042844  0.068300 -0.051918 -0.032073  0.005497  
12320  0.041603  0.035866  0.041392  0.160559 -0.034255  0.013175  0.098460  
12321  0

In [200]:
#df_umap = df_umap.sort_values(by='Label')

In [204]:
df_umap.drop_duplicates(subset=['Sequence','Affinity'], keep='first')

PDB                          Protein     Mutation  \
0      1CSE             Subtilisin Carlsberg          NaN   
1      1ACB        Bovine alpha-chymotrypsin          NaN   
2      1SBN                   Subtilisin BPN          NaN   
3      1SIB                   Subtilisin BPN          NaN   
4      1TM1                   Subtilisin BPN          NaN   
...     ...                              ...          ...   
12318  2WPT             Colicin E9 DNase_mut  DA33A,FB86A   
12319  2WPT  Colicin E2 immunity protein_mut        NA34A   
12320  2WPT             Colicin E9 DNase_mut        SB84A   
12321  2WPT             Colicin E9 DNase_mut  SB84A,NA34A   
12322  2WPT  Colicin E2 immunity protein_mut  SB84A,NA34A   

                                                Sequence  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      CGVPAIQPVLSGLSRIVNGEEAVPGSWPWQVSLQDKTGFHFCGGSL...   
2      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
3      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
4      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
...                                                  ...   
12318  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12319  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12320  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12321  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12322  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                                  PPI Label  Affinity  \
0                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
1                 Bovine alpha-chymotrypsin___Eglin c   wt1  1.49E-12   
2                            Subtilisin BPN___Eglin c   wt1   5.4E-11   
3                            Subtilisin BPN___Eglin c   wt1   1.1E-10   
4           Subtilisin BPN___Chymotrypsin inhibitor 2   wt1     2E-12   
...                                               ...   ...       ...   
12318  Colicin E2 immunity protein___Colicin E9 DNase   mut  6.21E-07   
12319  Colicin E9 DNase___Colicin E2 immunity protein   mut  6.49E-07   
12320  Colicin E2 immunity protein___Colicin E9 DNase   mut  7.09E-07   
12321  Colicin E2 immunity protein___Colicin E9 DNase   mut  3.92E-07   
12322  Colicin E9 DNase___Colicin E2 immunity protein   mut  3.92E-07   

              0         1         2  ...      1270      1271      1272  \
0     -0.032180 -0.156770 -0.000691  ... -0.009642 -0.058612  0.030370   
1     -0.024063 -0.075022  0.095781  ... -0.030885 -0.010721  0.019142   
2     -0.026634 -0.127109 -0.023703  ... -0.008960 -0.038177  0.030544   
3     -0.026634 -0.127109 -0.023703  ... -0.008960 -0.038177  0.030544   
4     -0.024246 -0.125899 -0.015986  ... -0.013187 -0.044538  0.007275   
...         ...       ...       ...  ...       ...       ...       ...   
12318 -0.023146 -0.030065 -0.042366  ...  0.028587 -0.030711  0.028562   
12319  0.040997  0.060716  0.011485  ...  0.061316 -0.110644 -0.032557   
12320 -0.024812 -0.034917 -0.039183  ...  0.032775 -0.029655  0.027244   
12321 -0.024812 -0.034917 -0.039183  ...  0.032775 -0.029655  0.027244   
12322  0.040997  0.060716  0.011485  ...  0.061316 -0.110644 -0.032557   

           1273      1274      1275      1276      1277      1278      1279  
0      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
1      0.011965 -0.024791 -0.073087  0.157850 -0.125122  0.007609  0.012032  
2     -0.026940 -0.018413 -0.092624  0.065720 -0.223058 -0.021946  0.083181  
3     -0.026940 -0.018413 -0.092624  0.065720 -0.223058 -0.021946  0.083181  
4      0.000478 -0.014124 -0.083644  0.048960 -0.228387 -0.020252  0.054023  
...         ...       ...       ...       ...       ...       ...       ...  
12318  0.041031  0.036093  0.043161  0.159644 -0.032207  0.014414  0.100678  
12319  0.077818  0.002379  0.042844  0.068300 -0.051918 -0.032073  0.005497  
12320  0.041603  0.035866  0.041392  0.160559 -0.034255  0.013175  0.098460  
12321  0

# alternative to generate concatenated scores
df_umap = np.concatenate((df_.wild_seq_1_embeddings, df_.wild_seq_2_embeddings, df_.mutant_seq_embeddings))
df_umap

In [205]:
features = df_umap.loc[:,0:]
features

0         1         2         3         4         5         6     \
0     -0.032180 -0.156770 -0.000691  0.196635 -0.085537  0.036425  0.051999   
1     -0.024063 -0.075022  0.095781  0.091304 -0.071632 -0.049195  0.119712   
2     -0.026634 -0.127109 -0.023703  0.160776 -0.056165 -0.017781  0.047966   
3     -0.026634 -0.127109 -0.023703  0.160776 -0.056165 -0.017781  0.047966   
4     -0.024246 -0.125899 -0.015986  0.149288 -0.057398 -0.010726  0.037149   
...         ...       ...       ...       ...       ...       ...       ...   
12318 -0.023146 -0.030065 -0.042366  0.004902 -0.033540 -0.052219  0.021217   
12319  0.040997  0.060716  0.011485  0.042063 -0.066023  0.053417 -0.009934   
12320 -0.024812 -0.034917 -0.039183  0.003409 -0.034276 -0.050773  0.022653   
12321 -0.024812 -0.034917 -0.039183  0.003409 -0.034276 -0.050773  0.022653   
12322  0.040997  0.060716  0.011485  0.042063 -0.066023  0.053417 -0.009934   

           7         8         9     ...      1270      1271      1272  \
0     -0.278995 -0.031392  0.134670  ... -0.009642 -0.058612  0.030370   
1     -0.103887 -0.073816  0.110430  ... -0.030885 -0.010721  0.019142   
2     -0.253847  0.008696  0.119804  ... -0.008960 -0.038177  0.030544   
3     -0.253847  0.008696  0.119804  ... -0.008960 -0.038177  0.030544   
4     -0.230619 -0.019392  0.123561  ... -0.013187 -0.044538  0.007275   
...         ...       ...       ...  ...       ...       ...       ...   
12318 -0.160497  0.014909  0.035471  ...  0.028587 -0.030711  0.028562   
12319  0.040825  0.072982 -0.072750  ...  0.061316 -0.110644 -0.032557   
12320 -0.158220  0.015947  0.033093  ...  0.032775 -0.029655  0.027244   
12321 -0.158220  0.015947  0.033093  ...  0.032775 -0.029655  0.027244   
12322  0.040825  0.072982 -0.072750  ...  0.061316 -0.110644 -0.032557   

           1273      1274      1275      1276      1277      1278      1279  
0      0.026104 -0.016590 -0.103824  0.098748 -0.207159 -0.001669  0.071841  
1      0.011965 -0.024791 -0.073087  0.157850 -0.125122  0.007609  0.012032  
2     -0.026940 -0.018413 -0.092624  0.065720 -0.223058 -0.021946  0.083181  
3     -0.026940 -0.018413 -0.092624  0.065720 -0.223058 -0.021946  0.083181  
4      0.000478 -0.014124 -0.083644  0.048960 -0.228387 -0.020252  0.054023  
...         ...       ...       ...       ...       ...       ...       ...  
12318  0.041031  0.036093  0.043161  0.159644 -0.032207  0.014414  0.100678  
12319  0.077818  0.002379  0.042844  0.068300 -0.051918 -0.032073  0.005497  
12320  0.041603  0.035866  0.041392  0.160559 -0.034255  0.013175  0.098460  
12321  0.041603  0.035866  0.041392  0.160559 -0.034255  0.013175  0.098460  
12322  0.077818  0.002379  0.042844  0.068300 -0.051918 -0.032073  0.005497  

[12323 rows x 1280 columns]

In [206]:
umap_2d = UMAP(n_components=2, init='random', random_state=0)
proj_2d = umap_2d.fit_transform(features)

In [207]:
results =  {'umap1': proj_2d[:,0], 'umap2': proj_2d[:,1]}
umap_results = pd.DataFrame(data=results)
umap_results

umap1      umap2
0       8.806902  16.833975
1       1.434421   7.185989
2       8.805940  16.833675
3       8.805256  16.833328
4      28.676891  10.290156
...          ...        ...
12318  -3.173853   0.516658
12319   7.278049 -15.190978
12320  -1.351963   1.392071
12321  -1.351869   1.392190
12322   7.281373 -15.188662

[12323 rows x 2 columns]

In [208]:
df_umap_ = pd.concat([df_umap, umap_results], axis=1)
df_umap_

PDB                          Protein     Mutation  \
0      1CSE             Subtilisin Carlsberg          NaN   
1      1ACB        Bovine alpha-chymotrypsin          NaN   
2      1SBN                   Subtilisin BPN          NaN   
3      1SIB                   Subtilisin BPN          NaN   
4      1TM1                   Subtilisin BPN          NaN   
...     ...                              ...          ...   
12318  2WPT             Colicin E9 DNase_mut  DA33A,FB86A   
12319  2WPT  Colicin E2 immunity protein_mut        NA34A   
12320  2WPT             Colicin E9 DNase_mut        SB84A   
12321  2WPT             Colicin E9 DNase_mut  SB84A,NA34A   
12322  2WPT  Colicin E2 immunity protein_mut  SB84A,NA34A   

                                                Sequence  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      CGVPAIQPVLSGLSRIVNGEEAVPGSWPWQVSLQDKTGFHFCGGSL...   
2      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
3      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
4      AQSVPYGVSQIKAPALHSQGYTGSNVKVAVIDSGIDSSHPDLKVAG...   
...                                                  ...   
12318  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12319  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12320  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12321  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12322  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                                  PPI Label  Affinity  \
0                      Subtilisin Carlsberg___Eglin c   wt1  1.12E-12   
1                 Bovine alpha-chymotrypsin___Eglin c   wt1  1.49E-12   
2                            Subtilisin BPN___Eglin c   wt1   5.4E-11   
3                            Subtilisin BPN___Eglin c   wt1   1.1E-10   
4           Subtilisin BPN___Chymotrypsin inhibitor 2   wt1     2E-12   
...                                               ...   ...       ...   
12318  Colicin E2 immunity protein___Colicin E9 DNase   mut  6.21E-07   
12319  Colicin E9 DNase___Colicin E2 immunity protein   mut  6.49E-07   
12320  Colicin E2 immunity protein___Colicin E9 DNase   mut  7.09E-07   
12321  Colicin E2 immunity protein___Colicin E9 DNase   mut  3.92E-07   
12322  Colicin E9 DNase___Colicin E2 immunity protein   mut  3.92E-07   

              0         1         2  ...      1272      1273      1274  \
0     -0.032180 -0.156770 -0.000691  ...  0.030370  0.026104 -0.016590   
1     -0.024063 -0.075022  0.095781  ...  0.019142  0.011965 -0.024791   
2     -0.026634 -0.127109 -0.023703  ...  0.030544 -0.026940 -0.018413   
3     -0.026634 -0.127109 -0.023703  ...  0.030544 -0.026940 -0.018413   
4     -0.024246 -0.125899 -0.015986  ...  0.007275  0.000478 -0.014124   
...         ...       ...       ...  ...       ...       ...       ...   
12318 -0.023146 -0.030065 -0.042366  ...  0.028562  0.041031  0.036093   
12319  0.040997  0.060716  0.011485  ... -0.032557  0.077818  0.002379   
12320 -0.024812 -0.034917 -0.039183  ...  0.027244  0.041603  0.035866   
12321 -0.024812 -0.034917 -0.039183  ...  0.027244  0.041603  0.035866   
12322  0.040997  0.060716  0.011485  ... -0.032557  0.077818  0.002379   

           1275      1276      1277      1278      1279      umap1      umap2  
0     -0.103824  0.098748 -0.207159 -0.001669  0.071841   8.806902  16.833975  
1     -0.073087  0.157850 -0.125122  0.007609  0.012032   1.434421   7.185989  
2     -0.092624  0.065720 -0.223058 -0.021946  0.083181   8.805940  16.833675  
3     -0.092624  0.065720 -0.223058 -0.021946  0.083181   8.805256  16.833328  
4     -0.083644  0.048960 -0.228387 -0.020252  0.054023  28.676891  10.290156  
...         ...       ...       ...       ...       ...        ...        ...  
12318  0.043161  0.159644 -0.032207  0.014414  0.100678  -3.173853   0.516658  
12319  0.042844  0.068300 -0.051918 -0.032073  0.005497   7.278049 -15.190978  
12320  0.041392  0.160559 -0.034255  0.013175  0.098460  -1.351963  

In [180]:
fig_2d = px.scatter(
    proj_2d, x=0, y=1,
    #color=df.species,
    #labels={'color': 'species'}
)
fig_2d.show()

In [215]:
import plotly.graph_objs as go
%matplotlib inline
color_dict = {'wt1':'#72B7B2', 'wt2':'#54A24B', 'mut':'#E45756'}
fig= px.scatter(
    df_umap_,
    x = 'umap1',
    y = 'umap2',
    color='Label',
    color_discrete_map=color_dict,
    hover_name='Protein',
    hover_data={
        'Protein': False,
        'PDB': True,
        'Label': True,
        'PPI': True,
        'Mutation':True,
        'Affinity':True,
        'umap1':False,
        'umap2':False
    }
)
fig.update_layout(template='simple_white',
                  title='SKEMPI Protein-Protein embeddings',
                  title_x=0.5
                  )
fig.show()

In [216]:
fig.write_html("skempi_ppi_plotly.html")

In [217]:
df_umap_.to_csv('protein_embeddings_for_umap.csv',index=False)

In [ ]:
"""visualize cosine similarity
between wt1---wt2 and wt1---mut
"""

In [242]:
df_

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12215  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
12216  2WPT           NA34A         6.49E-07         8.2E-07   
12217  2WPT           SB84A         7.09E-07         8.2E-07   
12218  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
12219  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                         Protein_1                    Protein_2  \
0             Subtilisin Carlsberg                      Eglin c   
1             Subtilisin Carlsberg                      Eglin c   
2             Subtilisin Carlsberg                      Eglin c   
3             Subtilisin Carlsberg                      Eglin c   
4             Subtilisin Carlsberg                      Eglin c   
...                            ...                          ...   
12215  Colicin E2 immunity protein             Colicin E9 DNase   
12216             Colicin E9 DNase  Colicin E2 immunity protein   
12217  Colicin E2 immunity protein             Colicin E9 DNase   
12218  Colicin E2 immunity protein             Colicin E9 DNase   
12219             Colicin E9 DNase  Colicin E2 immunity protein   

                                              wild_seq_1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12215  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12216  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12217  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12218  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12219  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                              wild_seq_2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                              mutant_seq  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                   wild_seq_1_embeddings  \
0      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
1      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
2      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
3      [[-0.03217955, -0.156769

In [227]:
test = df_.iloc[:5,:]
test

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0  1CSE           LI45G         5.26E-11        1.12E-12   
1  1CSE           LI45S         8.33E-12        1.12E-12   
2  1CSE           LI45P         1.02E-07        1.12E-12   
3  1CSE           LI45I         1.72E-10        1.12E-12   
4  1CSE           LI45D         1.92E-09        1.12E-12   

              Protein_1 Protein_2  \
0  Subtilisin Carlsberg   Eglin c   
1  Subtilisin Carlsberg   Eglin c   
2  Subtilisin Carlsberg   Eglin c   
3  Subtilisin Carlsberg   Eglin c   
4  Subtilisin Carlsberg   Eglin c   

                                          wild_seq_1  \
0  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   

                                          wild_seq_2  \
0  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   

                                          mutant_seq  \
0  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   

                               wild_seq_1_embeddings  \
0  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
1  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
2  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
3  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
4  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   

                               wild_seq_2_embeddings  \
0  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
1  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
2  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
3  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
4  [[0.05527322, -0.029942056, 0.032425687, -0.05...   

                               mutant_seq_embeddings  
0  [[0.05044703, -0.026978722, 0.027345372, -0.04...  
1  [[0.053682353, -0.024133433, 0.02780459, -0.04...  
2  [[0.05011466, -0.026969189, 0.025009282, -0.05...  
3  [[0.053000774, -0.027996115, 0.027281117, -0.0...  
4  [[0.052454446, -0.025797503, 0.02369322, -0.05...

In [228]:
representation_store_dict

{'YMDFDDDIPF': array([[ 0.13910443, -0.07379941, -0.29339817, ...,  0.00111225,
         -0.07300624, -0.07609034],
        [ 0.05488537, -0.12718895, -0.0194888 , ...,  0.01878373,
         -0.191497  ,  0.02732703],
        [ 0.06376954, -0.13735689, -0.09811898, ..., -0.12271725,
          0.07584549,  0.06119155],
        ...,
        [ 0.22345842,  0.10594463, -0.14535588, ..., -0.0300162 ,
          0.07676005, -0.06822958],
        [ 0.0684359 ,  0.16869766,  0.19172475, ..., -0.23958898,
         -0.07680969, -0.05274785],
        [-0.09126833,  0.14141782,  0.09173559, ..., -0.21092641,
         -0.06649562,  0.10675846]], dtype=float32),
 'ARTKQTARKS': array([[ 0.02447946,  0.01928901, -0.03956539, ...,  0.12661682,
         -0.09285621,  0.01617499],
        [ 0.10751038,  0.06919377,  0.12876596, ..., -0.00814786,
          0.02145161, -0.02784804],
        [ 0.00273106,  0.03329812,  0.06105419, ...,  0.07983748,
         -0.03923513, -0.00519595],
        ...,
        [ 0

In [240]:
from sklearn.metrics.pairwise import cosine_similarity
def calculate_cosine_similarity(seq1, seq2, wt2=False, mut=False):
    for key, value in representation_store_dict.items():
        if seq1 == key:
            rep_1 = value
            continue
    if wt2:
        for key, value in representation_store_dict_seq2.items():
            if seq2 == key:
                rep_2 = value
                continue
    elif mut:
        for key, value in representation_store_dict_mut.items():
            if seq2 == key:
                rep_2 = value
                continue
    else:
        raise TypeError
    cosine_1_2 = cosine_similarity(rep_1, rep_2, dense_output=True)
    return np.mean(cosine_1_2)
test['cosine_similarity_1_2'] = test.apply(lambda x:calculate_cosine_similarity(x['wild_seq_1'], x['wild_seq_2'],wt2=True),axis=1)
test['cosine_similarity_1_mut'] = test.apply(lambda x:calculate_cosine_similarity(x['wild_seq_1'], x['mutant_seq'],mut=True),axis=1)
test

/var/tmp/pbs.784522.hn-10-03/ipykernel_254365/2553169124.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/tmp/pbs.784522.hn-10-03/ipykernel_254365/2553169124.py:22: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0  1CSE           LI45G         5.26E-11        1.12E-12   
1  1CSE           LI45S         8.33E-12        1.12E-12   
2  1CSE           LI45P         1.02E-07        1.12E-12   
3  1CSE           LI45I         1.72E-10        1.12E-12   
4  1CSE           LI45D         1.92E-09        1.12E-12   

              Protein_1 Protein_2  \
0  Subtilisin Carlsberg   Eglin c   
1  Subtilisin Carlsberg   Eglin c   
2  Subtilisin Carlsberg   Eglin c   
3  Subtilisin Carlsberg   Eglin c   
4  Subtilisin Carlsberg   Eglin c   

                                          wild_seq_1  \
0  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4  AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   

                                          wild_seq_2  \
0  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   

                                          mutant_seq  \
0  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4  TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   

                               wild_seq_1_embeddings  \
0  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
1  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
2  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
3  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
4  [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   

                               wild_seq_2_embeddings  \
0  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
1  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
2  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
3  [[0.05527322, -0.029942056, 0.032425687, -0.05...   
4  [[0.05527322, -0.029942056, 0.032425687, -0.05...   

                               mutant_seq_embeddings  cosine_similarity_1_2  \
0  [[0.05044703, -0.026978722, 0.027345372, -0.04...               0.342936   
1  [[0.053682353, -0.024133433, 0.02780459, -0.04...               0.342936   
2  [[0.05011466, -0.026969189, 0.025009282, -0.05...               0.342936   
3  [[0.053000774, -0.027996115, 0.027281117, -0.0...               0.342936   
4  [[0.052454446, -0.025797503, 0.02369322, -0.05...               0.342936   

   cosine_similarity_1_mut  
0                 0.344894  
1                 0.343857  
2                 0.342939  
3                 0.343436  
4                 0.343914

In [259]:
dt = df_.copy()
dt['cosine_similarity_1_2'] = dt.apply(lambda x:calculate_cosine_similarity(x['wild_seq_1'], x['wild_seq_2'],wt2=True),axis=1)
dt['cosine_similarity_1_mut'] = dt.apply(lambda x:calculate_cosine_similarity(x['wild_seq_1'], x['mutant_seq'],mut=True),axis=1)
dt

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0      1CSE           LI45G         5.26E-11        1.12E-12   
1      1CSE           LI45S         8.33E-12        1.12E-12   
2      1CSE           LI45P         1.02E-07        1.12E-12   
3      1CSE           LI45I         1.72E-10        1.12E-12   
4      1CSE           LI45D         1.92E-09        1.12E-12   
...     ...             ...              ...             ...   
12215  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
12216  2WPT           NA34A         6.49E-07         8.2E-07   
12217  2WPT           SB84A         7.09E-07         8.2E-07   
12218  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
12219  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                         Protein_1                    Protein_2  \
0             Subtilisin Carlsberg                      Eglin c   
1             Subtilisin Carlsberg                      Eglin c   
2             Subtilisin Carlsberg                      Eglin c   
3             Subtilisin Carlsberg                      Eglin c   
4             Subtilisin Carlsberg                      Eglin c   
...                            ...                          ...   
12215  Colicin E2 immunity protein             Colicin E9 DNase   
12216             Colicin E9 DNase  Colicin E2 immunity protein   
12217  Colicin E2 immunity protein             Colicin E9 DNase   
12218  Colicin E2 immunity protein             Colicin E9 DNase   
12219             Colicin E9 DNase  Colicin E2 immunity protein   

                                              wild_seq_1  \
0      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4      AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                  ...   
12215  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12216  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12217  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12218  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12219  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                              wild_seq_2  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                              mutant_seq  \
0      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4      TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   
...                                                  ...   
12215  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12216  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
12217  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12218  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
12219  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                   wild_seq_1_embeddings  \
0      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
1      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
2      [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
3      [[-0.03217955, -0.156769

In [281]:
dt['protein_pairs_1_2'] = dt['Protein_1']+'_'+dt['Protein_2']
#dt['protein_pairs_1_mut'] = dt['Protein_1']+'_'+dt['Protein_2']+"_mut"
dt['protein_pairs_1_mut'] = dt['Protein_1']+'_'+dt['Protein_2']

In [282]:
dt = dt.reset_index(drop=True)
dt

pdb Mutation(s)_PDB Affinity_mut (M) Affinity_wt (M)  \
0     1CSE           LI45G         5.26E-11        1.12E-12   
1     1CSE           LI45S         8.33E-12        1.12E-12   
2     1CSE           LI45P         1.02E-07        1.12E-12   
3     1CSE           LI45I         1.72E-10        1.12E-12   
4     1CSE           LI45D         1.92E-09        1.12E-12   
...    ...             ...              ...             ...   
7182  2WPT     DA33A,FB86A         6.21E-07         8.2E-07   
7183  2WPT           NA34A         6.49E-07         8.2E-07   
7184  2WPT           SB84A         7.09E-07         8.2E-07   
7185  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   
7186  2WPT     SB84A,NA34A         3.92E-07         8.2E-07   

                        Protein_1                    Protein_2  \
0            Subtilisin Carlsberg                      Eglin c   
1            Subtilisin Carlsberg                      Eglin c   
2            Subtilisin Carlsberg                      Eglin c   
3            Subtilisin Carlsberg                      Eglin c   
4            Subtilisin Carlsberg                      Eglin c   
...                           ...                          ...   
7182  Colicin E2 immunity protein             Colicin E9 DNase   
7183             Colicin E9 DNase  Colicin E2 immunity protein   
7184  Colicin E2 immunity protein             Colicin E9 DNase   
7185  Colicin E2 immunity protein             Colicin E9 DNase   
7186             Colicin E9 DNase  Colicin E2 immunity protein   

                                             wild_seq_1  \
0     AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
1     AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
2     AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
3     AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
4     AQTVPYGIPLIKADKVQAQGFKGANVKVAVLDTGIQASHPDLNVVG...   
...                                                 ...   
7182  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
7183  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
7184  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
7185  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
7186  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   

                                             wild_seq_2  \
0     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
1     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
2     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
3     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
4     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTLD...   
...                                                 ...   
7182  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
7183  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   
7184  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
7185  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
7186  MELKHSISDYTEAEFLEFVKKIARAEGATECDDNKLVREFERLTEH...   

                                             mutant_seq  \
0     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTGD...   
1     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTSD...   
2     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTPD...   
3     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTID...   
4     TEFGSELKSFPEVVGKTVDQAREYFTLHYPQYNVYFLPEGSPVTDD...   
...                                                 ...   
7182  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
7183  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   
7184  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
7185  MESKRNKPGKATGKGKPVGDKWLDDAGKDSGAPIPDRIADKLRDKE...   
7186  MELKHSISDYTEAEFLEFVKKIARAEGATECDDAKLVREFERLTEH...   

                                  wild_seq_1_embeddings  \
0     [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
1     [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
2     [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
3     [[-0.03217955, -0.15676992, -0.0006907017, 0.1...   
4     [[-0.03217955, -0.15676992, -

In [283]:
dt_distances_1_2 = dt[['protein_pairs_1_2', 'cosine_similarity_1_2']].rename(columns={'protein_pairs_1_2':'protein_pairs', 'cosine_similarity_1_2':'cosine_similarity'})
label_wt = pd.Series(['wt']*len(dt['protein_pairs_1_2']), name='label')
dt_distances_1_2 = pd.concat([dt_distances_1_2, label_wt], axis=1)
dt_distances_1_mut = dt[['protein_pairs_1_mut', 'cosine_similarity_1_mut']].rename(columns={'protein_pairs_1_mut':'protein_pairs', 'cosine_similarity_1_mut':'cosine_similarity'})
label_mut = pd.Series(['mut']*len(dt['protein_pairs_1_mut']), name='label')
dt_distances_1_mut = pd.concat([dt_distances_1_mut, label_mut], axis=1)
combined_df = pd.concat([dt_distances_1_2, dt_distances_1_mut], axis=0).reset_index(drop=True)
combined_df

protein_pairs  cosine_similarity label
0                      Subtilisin Carlsberg_Eglin c           0.342936    wt
1                      Subtilisin Carlsberg_Eglin c           0.342936    wt
2                      Subtilisin Carlsberg_Eglin c           0.342936    wt
3                      Subtilisin Carlsberg_Eglin c           0.342936    wt
4                      Subtilisin Carlsberg_Eglin c           0.342936    wt
...                                             ...                ...   ...
14369  Colicin E2 immunity protein_Colicin E9 DNase           0.652275   mut
14370  Colicin E9 DNase_Colicin E2 immunity protein           0.651634   mut
14371  Colicin E2 immunity protein_Colicin E9 DNase           0.650213   mut
14372  Colicin E2 immunity protein_Colicin E9 DNase           0.650213   mut
14373  Colicin E9 DNase_Colicin E2 immunity protein           0.651634   mut

[14374 rows x 3 columns]

In [284]:
# Function to treat 'abc_def' and 'def_abc' as the same
def sort_sequence(prot_name):
    try:
        parts = prot_name.split('_')
    except AttributeError:
        print(prot_name)
    parts.sort()
    return '_'.join(parts)
combined_df['protein_pairs'] = combined_df['protein_pairs'].apply(sort_sequence)
final_df = combined_df.drop_duplicates(subset=['protein_pairs', 'cosine_similarity'], keep='first')
final_df

protein_pairs  cosine_similarity label
0                 Eglin c_Subtilisin Carlsberg           0.342936    wt
6            Bovine alpha-chymotrypsin_Eglin c           0.422878    wt
12                      Eglin c_Subtilisin BPN           0.349572    wt
13                      Eglin c_Subtilisin BPN           0.351778    wt
14     Chymotrypsin inhibitor 2_Subtilisin BPN           0.353510    wt
...                                        ...                ...   ...
14193                           ACTR_CREB NCBD           0.817230   mut
14322                           ACTR_CREB NCBD           0.772929   mut
14323                           ACTR_CREB NCBD           0.813427   mut
14345   Ephrin type-A receptor 2 SAM_SHIP2 SAM           0.489577   mut
14355                 HEW Lysozyme_HyHEL-5 fab           0.364362   mut

[2151 rows x 3 columns]

In [288]:
#color_dict = {'wt1':'#72B7B2', 'wt2':'#54A24B', 'mut':'#E45756'}
fig= px.scatter(
    final_df,
    x = 'protein_pairs',
    y = 'cosine_similarity',
    color = 'label'
)
fig.update_layout(template='simple_white',
                  title='SKEMPI Protein-Protein cosine similarities comparison',
                  title_x=0.5
                  )
fig.update_xaxes(tickangle=45)
fig.show()

In [290]:
fig.write_html('SKEMPI_pair-pair_cosine_similarity_comparison.html')

In [ ]:
pd.DataFrame(representation_store_dict['ARTKQTARKS'][0])

In [ ]:
if torch.cuda.is_available():
    batch_tokens = batch_tokens.to(device='cuda', non_blocking=True)
    model = model.cuda()
    print('Transferred model to GPU')

In [ ]:
output = self.model(tokens, repr_layers=repr_layers, return_contacts=return_contacts)

In [ ]:
batch_labels, batch_strs, batch_tokens = batch_converter(seqs_tuples_wt1)
if torch.cuda.is_available():
    batch_tokens = batch_tokens.to(device='cuda', non_blocking=True)
    model = model.cuda()
    print('Transferred model to GPU')
with torch.no_grad():
    output = model(batch_tokens, repr_layers=[33], return_contacts=False)